In [5]:
from einops import einsum   
import numpy as np
import torch
from typing import List
from cs336_basics.transformer_lm.my_transformer_block import my_transformer_block

In [6]:
np.set_printoptions(linewidth=300, threshold=np.inf)

In [ ]:
# def run_transformer_block(
#     d_model: int,
#     num_heads: int,
#     d_ff: int,
#     max_seq_len: int,
#     theta: float,
#     weights: dict[str, Tensor],
#     in_features: Float[Tensor, " batch sequence_length d_model"],
# ) -> Float[Tensor, " batch sequence_length d_model"]

In [16]:
# def ts_state_dict():
#     FIXTURES_PATH=r'C:\Users\Andres.DESKTOP-D77KM25\Documents\assignment1-basics\tests\fixtures'
#     import json
#     state_dict = torch.load(FIXTURES_PATH / "ts_tests" / "model.pt", map_location="cpu")
#     config = json.load(open(FIXTURES_PATH / "ts_tests" / "model_config.json"))
#     state_dict = {
#         k.replace('_orig_mod.', ''): v for k, v in state_dict.items()
#     }
#     return state_dict, config

In [17]:
def ts_state_dict():
    import torch
    import json
    import os
    from pathlib import Path
    
    # Convert string path to Path object
    FIXTURES_PATH = Path(r'C:\Users\Andres.DESKTOP-D77KM25\Documents\assignment1-basics\tests\fixtures')
    
    # Create paths using Path object
    model_path = FIXTURES_PATH / "ts_tests" / "model.pt"
    config_path = FIXTURES_PATH / "ts_tests" / "model_config.json"
    
    # Load state dict
    state_dict = torch.load(model_path, map_location="cpu")
    
    # Load config using context manager
    with open(config_path, 'r') as f:
        config = json.load(f)
    
    # Process the state dict
    state_dict = {
        k.replace('_orig_mod.', ''): v for k, v in state_dict.items()
    }
    
    return state_dict, config

In [19]:
ts_state_dict()

({'token_embeddings.weight': tensor([[ 0.6384, -0.3678,  0.2761,  ..., -0.1542, -0.6972,  0.4515],
          [ 0.2662, -0.5991,  0.7674,  ...,  0.4097, -0.8294,  0.0573],
          [-0.1292, -0.3024,  0.3630,  ...,  0.2060,  0.2291, -0.5387],
          ...,
          [ 0.9606, -0.2919, -0.0333,  ...,  0.0130, -0.6761, -0.3038],
          [ 0.5150,  0.1477,  0.3167,  ..., -0.0552, -0.8565, -0.3290],
          [-0.9148, -0.5046,  0.6417,  ...,  0.2892, -0.4009, -0.0566]]),
  'layers.0.attn.q_proj.weight': tensor([[ 0.0372, -0.0888,  0.2558,  ...,  0.0049, -0.2693, -0.1108],
          [ 0.0520,  0.0837, -0.0109,  ..., -0.0062, -0.0301,  0.0772],
          [ 0.1074, -0.0745,  0.0017,  ..., -0.0322,  0.0527, -0.0305],
          ...,
          [-0.1228,  0.0824,  0.0505,  ..., -0.1418,  0.0130, -0.0677],
          [ 0.1143,  0.1974, -0.1546,  ..., -0.1313,  0.0992, -0.1394],
          [-0.0936,  0.2000, -0.0574,  ..., -0.0828,  0.1563,  0.1365]]),
  'layers.0.attn.k_proj.weight': tensor([[ 0

In [20]:
block_weights = {k.replace("layers.0.", ""): v for k, v in ts_state_dict()[0].items() if "layers.0." in k}


In [21]:
block_weights

{'attn.q_proj.weight': tensor([[ 0.0372, -0.0888,  0.2558,  ...,  0.0049, -0.2693, -0.1108],
         [ 0.0520,  0.0837, -0.0109,  ..., -0.0062, -0.0301,  0.0772],
         [ 0.1074, -0.0745,  0.0017,  ..., -0.0322,  0.0527, -0.0305],
         ...,
         [-0.1228,  0.0824,  0.0505,  ..., -0.1418,  0.0130, -0.0677],
         [ 0.1143,  0.1974, -0.1546,  ..., -0.1313,  0.0992, -0.1394],
         [-0.0936,  0.2000, -0.0574,  ..., -0.0828,  0.1563,  0.1365]]),
 'attn.k_proj.weight': tensor([[ 0.0890,  0.1049,  0.0980,  ...,  0.1314,  0.0594, -0.0206],
         [ 0.0271,  0.0840, -0.2509,  ..., -0.3258,  0.1056,  0.1248],
         [-0.0607, -0.1607,  0.2255,  ...,  0.2126, -0.0026, -0.0891],
         ...,
         [-0.0115,  0.1092,  0.0310,  ..., -0.0912,  0.2021,  0.1031],
         [-0.0391, -0.1004,  0.1376,  ...,  0.0082, -0.0004,  0.1317],
         [-0.2910, -0.0298, -0.1720,  ..., -0.1184,  0.0639, -0.0232]]),
 'attn.v_proj.weight': tensor([[-0.0538, -0.0038, -0.0073,  ...,  0.1269

In [25]:
torch.manual_seed(4)
batch_size=4
n_queries=12
d_model=64
in_embeddings=torch.randn(batch_size, n_queries, d_model)
observed=my_transformer_block(d_model=64,
                     theta=10000.0,
                     num_heads=4,
                     d_ff=128,
                     max_seq_len=12,                     
                     weights=block_weights,
                     in_features=in_embeddings).forward(in_features=in_embeddings)
observed.shape


torch.Size([4, 12, 64])

In [36]:
expected = np.load(r'c:\Users\Andres.DESKTOP-D77KM25\Documents\assignment1-basics\tests\_snapshots\test_transformer_block.npz')
expected=expected['array']

In [37]:
expected.shape

(4, 12, 64)

In [38]:
observed_np=observed.detach().numpy()
expected_np=expected

In [39]:
print(observed_np.shape)
print(expected_np.shape)


(4, 12, 64)
(4, 12, 64)


In [51]:
# Convert tensors to numpy arrays for element-wise comparison
for batch in range(0,4):
    for tok_pos in range(0,12):
        # Calculate absolute differences
        abs_diff = np.abs(expected_np - observed_np)

        # Find indices where differences exceed tolerance
        tolerance = 1e-6
        diff_mask = abs_diff > tolerance
        diff_indices = np.where(diff_mask)

        # Print differences
        if len(diff_indices[0]) > 0:
            print(f"Found {len(diff_indices[0])} differences exceeding tolerance {tolerance}:")
            for i in range(len(diff_indices[0])):
                idx = tuple(dim[i] for dim in diff_indices)
                print(f"\nPosition {idx}:")
                print(f"Expected: {expected_np[idx]:.8f}")
                print(f"Observed: {observed_np[idx]:.8f}")
                print(f"Absolute difference: {abs_diff[idx]:.8f}")
        else:
            print("No differences found exceeding tolerance")

Found 2837 differences exceeding tolerance 1e-06:

Position (np.int64(0), np.int64(0), np.int64(0)):
Expected: 0.05866861
Observed: 0.05867672
Absolute difference: 0.00000811

Position (np.int64(0), np.int64(0), np.int64(1)):
Expected: 1.07168269
Observed: 1.07168114
Absolute difference: 0.00000155

Position (np.int64(0), np.int64(0), np.int64(2)):
Expected: -0.69693792
Observed: -0.69694197
Absolute difference: 0.00000405

Position (np.int64(0), np.int64(0), np.int64(3)):
Expected: -0.44198585
Observed: -0.44199091
Absolute difference: 0.00000507

Position (np.int64(0), np.int64(0), np.int64(4)):
Expected: 0.01280221
Observed: 0.01280072
Absolute difference: 0.00000149

Position (np.int64(0), np.int64(0), np.int64(6)):
Expected: -4.06088543
Observed: -4.06089401
Absolute difference: 0.00000858

Position (np.int64(0), np.int64(0), np.int64(7)):
Expected: 1.10056210
Observed: 1.10056508
Absolute difference: 0.00000298

Position (np.int64(0), np.int64(0), np.int64(8)):
Expected: -0.08589

KeyboardInterrupt: 

In [59]:
for batch in range(0,4):
    for tok_pos in range(0,12):
        # Calculate absolute differences
        abs_diff = np.abs(expected_np - observed_np)

        # Find indices where differences exceed tolerance
        tolerance = 1e-6
        diff_mask = abs_diff > tolerance
        diff_indices = np.where(diff_mask)

        # Print side by side comparison of differences
        if len(diff_indices[0]) > 0:
            print("\nDifferences exceeding tolerance:")
            print(f"{'Position':<20} {'Expected':<15} {'Observed':<15} {'Abs Diff':<15}")
            print("-" * 65)
            for i in range(len(diff_indices[0])):
                idx = tuple(dim[i] for dim in diff_indices)
                print(f"{str(idx):<20} {expected_np[idx]:< 15.8f} {observed_np[idx]:< 15.8f} {abs_diff[idx]:< 15.8f}")



Differences exceeding tolerance:
Position             Expected        Observed        Abs Diff       
-----------------------------------------------------------------
(np.int64(0), np.int64(0), np.int64(0))  0.05866861      0.05867672      0.00000811    
(np.int64(0), np.int64(0), np.int64(1))  1.07168269      1.07168114      0.00000155    
(np.int64(0), np.int64(0), np.int64(2)) -0.69693792     -0.69694197      0.00000405    
(np.int64(0), np.int64(0), np.int64(3)) -0.44198585     -0.44199091      0.00000507    
(np.int64(0), np.int64(0), np.int64(4))  0.01280221      0.01280072      0.00000149    
(np.int64(0), np.int64(0), np.int64(6)) -4.06088543     -4.06089401      0.00000858    
(np.int64(0), np.int64(0), np.int64(7))  1.10056210      1.10056508      0.00000298    
(np.int64(0), np.int64(0), np.int64(8)) -0.08589435     -0.08588868      0.00000566    
(np.int64(0), np.int64(0), np.int64(9))  0.43494380      0.43495008      0.00000629    
(np.int64(0), np.int64(0), np.int64(10)

In [58]:
tolerance = 1e-6
for batch in range(0,4):
    for tok_pos in range(0,12):
        # Calculate absolute differences
        abs_diff = np.abs(expected_np - observed_np)
        # Create list to store mismatches
        mismatches = []
        
        # Iterate through each position in the arrays
        for i in range(expected_np.shape[0]):
            for j in range(expected_np.shape[1]):
                for k in range(expected_np.shape[2]):
                    if abs_diff[i,j,k] > tolerance:
                        mismatches.append((i,j,k))
        
        # Convert list of tuples to tuple of arrays for numpy compatibility
        if mismatches:
            diff_indices = tuple(zip(*mismatches))
        else:
            diff_indices = tuple(np.array([]) for _ in range(expected_np.ndim))

        # Find indices where differences exceed tolerance and return them
        
        # diff_mask = abs_diff > tolerance
        # diff_indices = np.where(diff_mask)

mismatches

[(0, 0, 0),
 (0, 0, 1),
 (0, 0, 2),
 (0, 0, 3),
 (0, 0, 4),
 (0, 0, 6),
 (0, 0, 7),
 (0, 0, 8),
 (0, 0, 9),
 (0, 0, 10),
 (0, 0, 11),
 (0, 0, 12),
 (0, 0, 13),
 (0, 0, 14),
 (0, 0, 15),
 (0, 0, 16),
 (0, 0, 17),
 (0, 0, 19),
 (0, 0, 21),
 (0, 0, 22),
 (0, 0, 23),
 (0, 0, 25),
 (0, 0, 26),
 (0, 0, 27),
 (0, 0, 28),
 (0, 0, 29),
 (0, 0, 30),
 (0, 0, 31),
 (0, 0, 32),
 (0, 0, 34),
 (0, 0, 35),
 (0, 0, 36),
 (0, 0, 37),
 (0, 0, 39),
 (0, 0, 41),
 (0, 0, 42),
 (0, 0, 44),
 (0, 0, 45),
 (0, 0, 46),
 (0, 0, 47),
 (0, 0, 48),
 (0, 0, 49),
 (0, 0, 50),
 (0, 0, 51),
 (0, 0, 52),
 (0, 0, 53),
 (0, 0, 55),
 (0, 0, 56),
 (0, 0, 59),
 (0, 0, 60),
 (0, 0, 61),
 (0, 0, 62),
 (0, 1, 0),
 (0, 1, 1),
 (0, 1, 2),
 (0, 1, 3),
 (0, 1, 4),
 (0, 1, 5),
 (0, 1, 6),
 (0, 1, 7),
 (0, 1, 8),
 (0, 1, 9),
 (0, 1, 10),
 (0, 1, 11),
 (0, 1, 12),
 (0, 1, 13),
 (0, 1, 14),
 (0, 1, 15),
 (0, 1, 16),
 (0, 1, 17),
 (0, 1, 18),
 (0, 1, 19),
 (0, 1, 20),
 (0, 1, 21),
 (0, 1, 22),
 (0, 1, 23),
 (0, 1, 24),
 (0, 1, 25),
 (0, 